In [ ]:
import pandas as pd
import matplotlib.pyplot as plt

# 读取数据集
crime_data = pd.read_csv('seasonal_pattern.csv')

# 转换时间列为日期时间类型
crime_data['date'] = pd.to_datetime(crime_data['Date/Time Opened'])

# 按犯罪类型分组并计算每个季度的犯罪数量
crime_data_grouped = crime_data.groupby(['Primary Category', pd.Grouper(key='date', freq='M')])['Primary Category'].count().unstack()

# 绘制每个季度的犯罪数量柱状图
crime_data_grouped.plot(kind='bar', figsize=(10,6))

# 添加标题和标签
plt.title('Crime by Season')
plt.xlabel('Season')
plt.ylabel('Number of Crimes')

# 显示图表
plt.show()

In [ ]:
import pandas as pd
import statsmodels.api as sm

# 读取数据
crime_data = pd.read_csv('2019-2021.csv')

# 将日期列转换为数字格式
crime_data['Date'] = pd.to_datetime(crime_data['Date/Time Opened'], format='%d/%m/%Y %H:%M')
crime_data = crime_data[pd.notna(crime_data['Date'])] # 过滤掉空值
crime_data['Date'] = crime_data['Date'].apply(pd.Timestamp.timestamp).astype(int)

# 将数据按日期排序
crime_data.sort_values('Date', inplace=True)

# 将日期列作为索引
crime_data.set_index('Date', inplace=True)

# 进行季节性分解
decomposition = sm.tsa.seasonal_decompose(crime_data, model='additive', period=12)

In [ ]:
import pandas as pd
import matplotlib.pyplot as plt
from statsmodels.tsa.arima.model import ARIMA
from sklearn.metrics import mean_squared_error
import statsmodels.api as sm

# 读取数据
crime_data = pd.read_csv('seasonal_pattern.csv')

# 将日期列转换为 datetime 类型
crime_data['date'] = pd.to_datetime(crime_data['Date/Time Opened 月'], format='%Y年%m月')

# 将日期列设置为索引
crime_data = crime_data.set_index('date')

# 检查是否有重复索引值
if crime_data.index.duplicated().any():
    crime_data = crime_data[~crime_data.index.duplicated(keep='first')]

# 进行季节性分解
res = sm.tsa.seasonal_decompose(crime_data, model='additive', period=12)

# 获取平稳时间序列
ts = res.resid.dropna()

# 绘制自相关和偏自相关函数图
fig, ax = plt.subplots(2,1, figsize=(10,6))
sm.graphics.tsa.plot_acf(ts, ax=ax[0])
sm.graphics.tsa.plot_pacf(ts, ax=ax[1])
plt.show()

# 设置ARIMA模型的参数
p = 2  # 自回归项
d = 0  # 差分阶数
q = 2  # 移动平均项
P = 1  # 季节性自回归项
D = 0  # 季节性差分阶数
Q = 1  # 季节性移动平均项
s = 4  # 季节性周期

# 建立ARIMA模型
model = sm.tsa.statespace.SARIMAX(crime_data, order=(p,d,q), seasonal_order=(P,D,Q,s))

# 拟合ARIMA模型
results = model.fit()

# 对测试数据进行预测
start_index = '2021-01-01'
end_index = '2021-12-31'
pred = results.predict(start=start_index, end=end_index)

# 绘制预测结果
fig, ax = plt.subplots(figsize=(10,6))
ax.plot(crime_data.index, crime_data['Primary Category'], label='Observed')
ax.plot(pred.index, pred, label='Predicted')
ax.legend()
plt.show()

# 评估模型性能
mse = mean_squared_error


In [13]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from scipy.stats import ttest_ind

# 读取数据文件
data = pd.read_csv('seasonal_pattern_count.csv')

# 数据预处理
data['Month'] = pd.to_datetime(data['Month'])
data['Season'] = np.where(data['Month'].dt.month.isin([3, 4, 5]), 'Spring',
                          np.where(data['Month'].dt.month.isin([6, 7, 8]), 'Summer',
                                   np.where(data['Month'].dt.month.isin([9, 10, 11]), 'Autumn', 'Winter')))
data_violent = data[data['Primary category'] == 'Assault']
data_property = data[data['Primary category'] == 'Student Welfare Concerns']

# 可视化分析
plt.figure(figsize=(10, 5))
plt.subplot(121)
sns.boxplot(x='Season', y='Count', data=data_violent)
plt.title('Boxplot of violent crime by season')
plt.subplot(122)
sns.boxplot(x='Season', y='Count', data=data_property)
plt.title('Boxplot of property crime by season')
plt.tight_layout()
plt.show()

# 假设检验
summer_violent = data_violent[data_violent['Season'] == 'Summer']['Count']
winter_violent = data_violent[data_violent['Season'] == 'Winter']['Count']
summer_property = data_property[data_property['Season'] == 'Summer']['Count']
winter_property = data_property[data_property['Season'] == 'Winter']['Count']

print("Violent crime - Summer vs. Winter")
print(ttest_ind(summer_violent, winter_violent))
print("Property crime - Winter vs. Summer")
print(ttest_ind(winter_property, summer_property))


In [1]:
import pandas as pd

crime_data = pd.read_csv("seasonal_pattern_count.csv")
print(crime_data.head())

   Year  Month          Primary Category  Count
0  2019      1  Student Welfare Concerns      3
1  2019      2  Student Welfare Concerns     10
2  2019      3  Student Welfare Concerns     16
3  2019      4  Student Welfare Concerns      7
4  2019      5  Student Welfare Concerns     15


通过筛选夏季和冬季月份的方式来计算每个季节的犯罪数量，并查看是否存在差异。

夏季为12月至2月，冬季为6月至8月。

In [11]:
# Create a new column indicating the season for each month
def get_season(month):
    if month in [12, 1, 2]:
        return "Summer"
    elif month in [3, 4, 5]:
        return "Autumn"
    elif month in [6, 7, 8]:
        return "Winter"
    else:
        return "Spring"

crime_data["Season"] = crime_data["Month"].apply(get_season)

# Group the data by season and primary category, and sum the counts
seasonal_data = crime_data.groupby(["Season", "Primary Category"])["Count"].sum().reset_index()
print(seasonal_data)

   Season          Primary Category  Count
0  Autumn                   Assault    717
1  Autumn  Student Welfare Concerns    107
2  Spring                   Assault    667
3  Spring  Student Welfare Concerns    154
4  Summer                   Assault    390
5  Summer  Student Welfare Concerns     79
6  Winter                   Assault    625
7  Winter  Student Welfare Concerns    125


暴力犯罪数量最高的季节是秋季717，其次是春季667。对于财产犯罪的数据，最多是春季154，其次是冬季125。

犯罪类型的季节趋势还可能因地理位置和其他因素而异。

In [7]:
import pandas as pd
from scipy.stats import ttest_ind

# read data from csv file
data = pd.read_csv('seasonal_pattern_count.csv')

# split data by season
summer_data = data[data['Month'].isin([12, 1, 2])]
winter_data = data[data['Month'].isin([6, 7, 8])]

# perform t-test
t_stat, p_val = ttest_ind(summer_data['Count'], winter_data['Count'])

# print results
print('T-statistic:', t_stat)
print('P-value:', p_val)
if p_val < 0.1:
    print('There is a significant difference between the mean counts of violent crime and property crime in summer and winter months.')
else:
    print('There is no significant difference between the mean counts of violent crime and property crime in summer and winter months.')


T-statistic: -1.212027769762644
P-value: 0.23385749270290088
There is no significant difference between the mean counts of violent crime and property crime in summer and winter months.


原假设（零假设）：夏季暴力犯罪发生的频率不比冬季高

备择假设：夏季暴力犯罪发生的频率比冬季高

In [2]:
import pandas as pd
from scipy.stats import ttest_ind

# 加载数据集
crime_data = pd.read_csv('seasonal_pattern_count.csv')

# 筛选出暴力犯罪的数据
assault_data = crime_data[crime_data['Primary Category'] == 'Assault']

# 计算夏季和冬季的暴力犯罪频率
summer_assault_rate = assault_data[(assault_data['Month'] == 12) | (assault_data['Month'] == 1) | (assault_data['Month'] == 2)]['Count'].mean()
winter_assault_rate = assault_data[(assault_data['Month'] == 6) | (assault_data['Month'] == 7) | (assault_data['Month'] == 8)]['Count'].mean()

# 打印夏季和冬季的频率
print('Summer assault rate:', summer_assault_rate)
print('Winter assault rate:', winter_assault_rate)

# 进行假设检验
t_stat, p_value = ttest_ind(assault_data[(assault_data['Month'] == 12) | (assault_data['Month'] == 1) | (assault_data['Month'] == 2)]['Count'], 
                            assault_data[(assault_data['Month'] == 6) | (assault_data['Month'] == 7) | (assault_data['Month'] == 8)]['Count'])

# 打印假设检验结果
print('t-statistic:', t_stat)
print('p-value:', p_value)

if p_value < 0.05:
    print('Reject null hypothesis')
else:
    print('Cannot reject null hypothesis')


Summer assault rate: 43.333333333333336
Winter assault rate: 69.44444444444444
t-statistic: -1.2632309233931294
p-value: 0.22460447401837833
Cannot reject null hypothesis


原假设（零假设）：冬季财产犯罪发生的频率不比夏季高

备择假设：冬季财产犯罪发生的频率比夏季高。

In [12]:
import pandas as pd
from scipy.stats import ttest_ind

# 加载数据集
crime_data = pd.read_csv('seasonal_pattern_count.csv')

# 筛选出财产犯罪的数据
welfare_data = crime_data[crime_data['Primary Category'] == 'Student Welfare Concerns']

# 计算夏季和冬季的财产犯罪频率
summer_welfare_rate = welfare_data[(welfare_data['Month'] == 12) | (welfare_data['Month'] == 1) | (welfare_data['Month'] == 2)]['Count'].mean()
winter_welfare_rate = welfare_data[(welfare_data['Month'] == 6) | (welfare_data['Month'] == 7) | (welfare_data['Month'] == 8)]['Count'].mean()

# 打印夏季和冬季的频率
print('Summer welfare rate:', summer_welfare_rate)
print('Winter welfare rate:', winter_welfare_rate)

# 进行假设检验
t_stat, p_value = ttest_ind(welfare_data[(welfare_data['Month'] == 6) | (welfare_data['Month'] == 7) | (welfare_data['Month'] == 8)]['Count'], 
                            welfare_data[(welfare_data['Month'] == 12) | (welfare_data['Month'] == 1) | (welfare_data['Month'] == 2)]['Count'])

# 打印假设检验结果
print('t-statistic:', t_stat)
print('p-value:', p_value)

if p_value < 0.05:
    print('Reject null hypothesis')
else:
    print('Cannot reject null hypothesis')

Summer welfare rate: 8.777777777777779
Winter welfare rate: 13.88888888888889
t-statistic: 1.5938055359530452
p-value: 0.13054032867847798
Cannot reject null hypothesis


In [7]:
import nltk

In [5]:
nltk.download('punkt')

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\MOC\AppData\Roaming\nltk_data...
[nltk_data]   Unzipping tokenizers\punkt.zip.


True

In [2]:
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\MOC\AppData\Roaming\nltk_data...
[nltk_data]   Unzipping corpora\stopwords.zip.


True

In [4]:
nltk.download('vader_lexicon')

[nltk_data] Downloading package vader_lexicon to
[nltk_data]     C:\Users\MOC\AppData\Roaming\nltk_data...


True

In [5]:
import pandas as pd
import nltk
from nltk.tokenize import sent_tokenize, word_tokenize
from nltk.corpus import stopwords
from nltk.probability import FreqDist
from nltk.sentiment import SentimentIntensityAnalyzer

# 读取表格数据
data = pd.read_csv('2019-2021.csv')
summary_column = data['Summary of the Incident (External Distribution)']

# 分句
sentences = [sent for summary in summary_column for sent in sent_tokenize(str(summary))]

# 分词和去除停用词
stop_words = set(stopwords.words('english'))
word_tokens = [word.lower() for sent in sentences for word in word_tokenize(sent) if word.isalpha() and word.lower() not in stop_words]

# 统计词频
freq_dist = FreqDist(word_tokens)

# 情感分析
sentiment_analyzer = SentimentIntensityAnalyzer()
sentiment_scores = [sentiment_analyzer.polarity_scores(sent) for sent in sentences]

# 打印分析结果
for i, sent in enumerate(sentences):
    print("Sentence:", sent)
    print("Sentiment Score:", sentiment_scores[i])
    print()

# 打印词频统计结果
print("Word Frequency:")
for word, frequency in freq_dist.items():
    print(word + ":", frequency)


Sentence: Emergency Services reported to HSD On Call of potential Gas Leak within School Grounds.
Sentiment Score: {'neg': 0.294, 'neu': 0.706, 'pos': 0.0, 'compound': -0.6124}

Sentence: Principal has been advised.
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: Gas Mains have been switched off
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: An executive staff member reported #### students were allegedly involved in an incident involving malcious damage.
Sentiment Score: {'neg': 0.176, 'neu': 0.824, 'pos': 0.0, 'compound': -0.4939}

Sentence: Another student filmed and uploaded the incident to a social media platform.
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: Police are investigating the matter.
Sentiment Score: {'neg': 0.0, 'neu': 0.784, 'pos': 0.216, 'compound': 0.0258}

Sentence: The Director of Educational Leadership has been notified.
Sentiment Score: {'neg': 0.0, 'neu': 1.


Sentence: School is managing the matter.
Sentiment Score: {'neg': 0.0, 'neu': 0.784, 'pos': 0.216, 'compound': 0.0258}

Sentence: Supports are in place.
Sentiment Score: {'neg': 0.0, 'neu': 0.545, 'pos': 0.455, 'compound': 0.3612}

Sentence: Executive staff and Director, Educational Leadership are aware.
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: An executive staff member reported a student exhibited risk taking behaviours and then absconded from school grounds.
Sentiment Score: {'neg': 0.123, 'neu': 0.877, 'pos': 0.0, 'compound': -0.2732}

Sentence: Parent was contacted.
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: The student's whereabout is unknown.
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: Police will be contacted.
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: Supports will be put in placed for the student involved.
Sentiment Score

Sentiment Score: {'neg': 0.0, 'neu': 0.737, 'pos': 0.263, 'compound': 0.3612}

Sentence: #### reporting will be conducted.
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: School is managing the matter at a local level.
Sentiment Score: {'neg': 0.0, 'neu': 0.864, 'pos': 0.136, 'compound': 0.0258}

Sentence: Executive staff are aware.
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: Executive staff report the school has ceased operations as a result of flooding in the area.
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: No injuries were sustained.
Sentiment Score: {'neg': 0.423, 'neu': 0.577, 'pos': 0.0, 'compound': -0.296}

Sentence: There are no staff or students remaining on school grounds.
Sentiment Score: {'neg': 0.196, 'neu': 0.804, 'pos': 0.0, 'compound': -0.296}

Sentence: Director, Educational Leadership is aware.
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound':

Sentence: #### reporting has been followed.
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: #####
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: Employee reports a student sustained injuries after being physically assaulted by a group of students on school grounds.
Sentiment Score: {'neg': 0.185, 'neu': 0.815, 'pos': 0.0, 'compound': -0.5267}

Sentence: Media unit will be informed as the incident was filmed by a student.
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: The school is managing the matter and supports are in place.
Sentiment Score: {'neg': 0.0, 'neu': 0.714, 'pos': 0.286, 'compound': 0.3818}

Sentence: Executive staff are aware.
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: An Executive member reports a utility failure on school grounds.
Sentiment Score: {'neg': 0.292, 'neu': 0.708, 'pos': 0.0, 'compound': -0.5106}

Sentence: Reporting 

Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: An executive staff member reports a utility failure on school grounds.
Sentiment Score: {'neg': 0.268, 'neu': 0.732, 'pos': 0.0, 'compound': -0.5106}

Sentence: External provider contacted, attended and rectified the failure.
Sentiment Score: {'neg': 0.32, 'neu': 0.68, 'pos': 0.0, 'compound': -0.5106}

Sentence: No physical injuries sustained.
Sentiment Score: {'neg': 0.423, 'neu': 0.577, 'pos': 0.0, 'compound': -0.296}

Sentence: No impact to school operations.
Sentiment Score: {'neg': 0.355, 'neu': 0.645, 'pos': 0.0, 'compound': -0.296}

Sentence: #### reporting will be followed.
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: Director, Educational Leadership will be notified.
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: Executive staff reporting welfare concerns for a student who has #####ed on school grounds.
Sentiment Score: {'neg

...

Sentiment Score: {'neg': 0.0, 'neu': 0.845, 'pos': 0.155, 'compound': 0.0258}

Sentence: An employee reports being #### by a student in a heightened state on school grounds.
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: No first aid required.
Sentiment Score: {'neg': 0.423, 'neu': 0.577, 'pos': 0.0, 'compound': -0.296}

Sentence: School executive staff is aware.
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: A student was in possession of a ####, on school grounds.
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: ####.
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: The incident will be reported to police.
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: The matter is also being managed locally.
Sentiment Score: {'neg': 0.0, 'neu': 0.845, 'pos': 0.155, 'compound': 0.0258}

Sentence: Support is in place.
Sentiment Scor

Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: #### staff aware.
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: An employee has been impacted after ##### by a student on school grounds.
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: Time has been lost, and supports are in place.
Sentiment Score: {'neg': 0.195, 'neu': 0.593, 'pos': 0.212, 'compound': 0.0516}

Sentence: Student's parents have been notified and the incident has been managed locally.
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: School ##### staff is aware.
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: #### ####.
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: Employee reports sustaining a minor injury due to #### for a student in a #####.
Sentiment Score: {'neg': 0.203, 'neu': 0.797, 'pos': 0.0, 'compound': -0.4215

Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: Two students were involved in ####### on school grounds.
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: First aid was administered and one student has absconded.
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: The Parents of the absconded student are aware and Police will be informed.
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: ####### will be advised.
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: Employee reported utility failures due to big storm and lightnings in the school grounds/premises.
Sentiment Score: {'neg': 0.188, 'neu': 0.812, 'pos': 0.0, 'compound': -0.4588}

Sentence: Students and staff members remained in the school.
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: Utility services are contacted.
Sentiment Score: {'n

Sentence: Parents were contacted.
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: #### #### #### #### and the student was #### #### #### ####.
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: #### the student was fine and able to remain at school.
Sentiment Score: {'neg': 0.0, 'neu': 0.847, 'pos': 0.153, 'compound': 0.2023}

Sentence: The school is undertaking a #####at this time.
Sentiment Score: {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}

Sentence: A student has been found in possession of a weapon on school grounds.
Sentiment Score: {'neg': 0.18, 'neu': 0.82, 'pos': 0.0, 'compound': -0.296}

Sentence: No specific threats or injuries sustained.
Sentiment Score: {'neg': 0.556, 'neu': 0.444, 'pos': 0.0, 'compound': -0.6124}

Sentence: Weapon has been confiscated and is with school ####### staff.
Sentiment Score: {'neg': 0.196, 'neu': 0.804, 'pos': 0.0, 'compound': -0.296}

Sentence: Parents have been notified

deputy: 33
admin: 1
electrical: 23
points: 3
cords: 1
monitoring: 17
classrooms: 14
winds: 4
knock: 1
lines: 4
wet: 1
electricians: 2
authorised: 4
locations: 15
repaired: 7
trees: 5
authority: 10
near: 9
distinguishing: 1
otherwise: 2
hazard: 3
consult: 1
structural: 8
go: 19
contained: 5
developed: 9
symptoms: 13
immediate: 6
meeting: 39
minors: 1
hugging: 1
disco: 1
interruption: 1
extended: 2
issued: 5
alternate: 3
method: 1
clothing: 25
attends: 4
past: 3
branch: 2
night: 10
climb: 1
run: 12
days: 9
gave: 10
precautionary: 3
measure: 4
fix: 4
avail: 1
torrential: 1
downpour: 2
hail: 3
flash: 1
heighten: 1
directly: 3
relocated: 7
complied: 4
collection: 12
window: 3
rocks: 1
expressing: 6
entry: 3
wont: 1
barricaded: 1
relative: 7
complete: 4
raised: 2
likely: 1
escort: 2
parts: 6
excecutive: 1
structure: 2
supposedly: 1
chased: 1
caring: 76
gum: 1
arrange: 3
removal: 2
danger: 2
uniform: 3
photo: 5
shaken: 4
branches: 5
two: 339
career: 1
families: 5
referred: 4
interrupted: 2
re

In [8]:
import pandas as pd
import nltk
from nltk.tokenize import sent_tokenize, word_tokenize
from nltk.corpus import stopwords
from nltk.probability import FreqDist
from nltk.sentiment import SentimentIntensityAnalyzer
from collections import Counter

# 读取表格数据
data = pd.read_csv('2019-2021.csv')
summary_column = data['Summary of the Incident (External Distribution)']

# 分句
sentences = [sent for summary in summary_column for sent in sent_tokenize(str(summary))]

# 分词和去除停用词
stop_words = set(stopwords.words('english'))
word_tokens = [word.lower() for sent in sentences for word in word_tokenize(sent) if word.isalpha() and word.lower() not in stop_words]

# 计算词频
word_freq = Counter(word_tokens)

# 按词频降序排列
sorted_word_freq = sorted(word_freq.items(), key=lambda x: x[1], reverse=True)

# 打印结果
for word, freq in sorted_word_freq:
    print(f"Word: {word}\tFrequency: {freq}")

Word: student	Frequency: 10738
Word: school	Frequency: 9114
Word: staff	Frequency: 4889
Word: grounds	Frequency: 4053
Word: parents	Frequency: 3450
Word: executive	Frequency: 3386
Word: students	Frequency: 3357
Word: notified	Frequency: 3248
Word: police	Frequency: 3025
Word: contacted	Frequency: 2915
Word: employee	Frequency: 2660
Word: aware	Frequency: 2609
Word: reports	Frequency: 2574
Word: director	Frequency: 2343
Word: place	Frequency: 2294
Word: member	Frequency: 2189
Word: aid	Frequency: 2124
Word: first	Frequency: 2122
Word: leadership	Frequency: 2110
Word: educational	Frequency: 2101
Word: supports	Frequency: 2082
Word: sustained	Frequency: 2070
Word: injuries	Frequency: 1607
Word: incident	Frequency: 1520
Word: another	Frequency: 1486
Word: matter	Frequency: 1360
Word: followed	Frequency: 1341
Word: managing	Frequency: 1309
Word: assaulted	Frequency: 1234
Word: xxxxx	Frequency: 1109
Word: reported	Frequency: 1037
Word: informed	Frequency: 1008
Word: support	Frequency: 964
Wo

In [17]:
import pandas as pd
import nltk
from nltk.tokenize import word_tokenize, sent_tokenize
from nltk import ne_chunk

# 读取CSV文件
data = pd.read_csv('2019-2021.csv')

# 提取Summary of the Incident列的文本数据
incident_summary = data['Summary of the Incident (External Distribution)']

# 执行命名实体识别
for sentence in incident_summary:
    tokens = word_tokenize(sentence)
    tagged = nltk.pos_tag(tokens)
    entities = ne_chunk(tagged)
    print(entities)



(S
  (ORGANIZATION Emergency/NN Services/NNPS)
  reported/VBD
  to/TO
  (ORGANIZATION HSD/NNP On/IN Call/NNP)
  of/IN
  potential/JJ
  Gas/NNP
  Leak/NNP
  within/IN
  (ORGANIZATION School/NNP Grounds/NNPS)
  ./.
  (PERSON Principal/NNP)
  has/VBZ
  been/VBN
  advised/VBN
  ./.
  (PERSON Gas/NNP Mains/NNP)
  have/VBP
  been/VBN
  switched/VBN
  off/RP)
(S
  An/DT
  executive/JJ
  staff/NN
  member/NN
  reported/VBD
  #/#
  #/#
  #/#
  #/#
  students/NNS
  were/VBD
  allegedly/RB
  involved/VBN
  in/IN
  an/DT
  incident/NN
  involving/VBG
  malcious/JJ
  damage/NN
  ./.
  Another/DT
  student/NN
  filmed/VBN
  and/CC
  uploaded/VBD
  the/DT
  incident/NN
  to/TO
  a/DT
  social/JJ
  media/NNS
  platform/NN
  ./.
  Police/NNP
  are/VBP
  investigating/VBG
  the/DT
  matter/NN
  ./.
  The/DT
  Director/NNP
  of/IN
  (ORGANIZATION Educational/NNP Leadership/NNP)
  has/VBZ
  been/VBN
  notified/VBN
  ./.
  (PERSON Media/NNP Unit/NNP)
  will/MD
  be/VB
  notified/VBN
  ./.)
(S
  An/DT
  Exe

(S
  Executive/JJ
  staff/NN
  member/NN
  reports/NNS
  due/JJ
  to/TO
  demolition/NN
  work/NN
  being/VBG
  carried/VBN
  out/IN
  the/DT
  school/NN
  will/MD
  be/VB
  non/JJ
  operational/JJ
  today/NN
  ./.
  Parents/NNS
  are/VBP
  aware/JJ
  ./.
  (PERSON Media/NNP Unit/NNP)
  advised/VBD
  ./.
  (PERSON Executive/NNP Director/NNP)
  has/VBZ
  been/VBN
  notified/VBN
  ./.)
(S
  An/DT
  executive/JJ
  staff/NN
  member/NN
  reports/VBZ
  a/DT
  utility/NN
  failure/NN
  to/TO
  the/DT
  fire/NN
  panels/NNS
  on/IN
  school/NN
  grounds/NNS
  ./.
  (PERSON Fire/NNP Brigade/NNP)
  attended/VBD
  and/CC
  are/VBP
  investigating/VBG
  the/DT
  matter/NN
  ./.
  Nil/NNP
  injuries/NNS
  sustained/VBD
  ./.
  Director/NNP
  ,/,
  (ORGANIZATION Educational/NNP Leadership/NNP)
  is/VBZ
  aware/JJ
  ./.)
(S
  An/DT
  Executive/JJ
  staff/NN
  member/NN
  reported/VBD
  a/DT
  student/NN
  absconded/VBN
  from/IN
  transport/NN
  on/IN
  the/DT
  way/NN
  to/TO
  school/NN
  and/CC
 

(S
  Executive/JJ
  staff/NN
  reports/NNS
  wellbeing/VBG
  concerns/NNS
  for/IN
  a/DT
  student/NN
  who/WP
  absconded/VBD
  from/IN
  school/NN
  grounds/NNS
  ./.
  The/DT
  student/NN
  's/POS
  whereabouts/NNS
  are/VBP
  currently/RB
  unknown/JJ
  ./.
  Parents/NNS
  have/VBP
  been/VBN
  notified/VBN
  ./.
  Police/NNP
  were/VBD
  contacted/VBN
  ./.
  Supports/NNS
  are/VBP
  in/IN
  place/NN
  ./.
  The/DT
  Director/NNP
  ,/,
  (ORGANIZATION Educational/NNP Leadership/NNP)
  will/MD
  be/VB
  made/VBN
  aware/JJ
  ./.)
(S
  An/DT
  executive/JJ
  staff/NN
  member/NN
  has/VBZ
  been/VBN
  assaulted/VBN
  by/IN
  a/DT
  student/NN
  which/WDT
  resulted/VBD
  in/IN
  a/DT
  lock/NN
  down/RP
  on/IN
  school/NN
  grounds/NNS
  ./.
  No/DT
  injuries/NNS
  reported/VBD
  and/CC
  first/JJ
  aid/NN
  was/VBD
  not/RB
  required/VBN
  ./.
  (PERSON Parent/NNP)
  notified/VBD
  and/CC
  student/NN
  was/VBD
  collected/VBN
  from/IN
  school/NN
  ./.
  Supports/NNS
  are/VB

(S
  Executive/JJ
  staff/NN
  member/NN
  reports/NNS
  of/IN
  a/DT
  student/NN
  in/IN
  a/DT
  #/#
  #/#
  #/#
  #/#
  state/NN
  demonstrating/VBG
  aggressive/JJ
  behaviours/NNS
  which/WDT
  resulted/VBD
  in/IN
  a/DT
  staff/NN
  member/NN
  being/VBG
  impacted/VBN
  ./.
  (PERSON School/NNP)
  was/VBD
  placed/VBN
  into/IN
  lockdown/NN
  for/IN
  a/DT
  brief/JJ
  period/NN
  ./.
  Nil/NNP
  injuries/NNS
  sustained/VBD
  ./.
  Supports/NNS
  in/IN
  place/NN
  ./.
  Director/NNP
  ,/,
  (ORGANIZATION Educational/NNP Leadership/NNP)
  will/MD
  be/VB
  advised/VBN
  ./.)
(S
  An/DT
  executive/JJ
  staff/NN
  member/NN
  reports/NNS
  that/WDT
  #/#
  #/#
  #/#
  #/#
  students/NNS
  have/VBP
  sustained/VBN
  an/DT
  injuries/NNS
  following/VBG
  an/DT
  assault/NN
  by/IN
  a/DT
  student/NN
  on/IN
  school/NN
  grounds/NNS
  ./.
  First-aid/NNP
  applied/VBD
  ./.
  Emergency/NN
  services/NNS
  were/VBD
  notified/VBN
  ./.
  A/DT
  student/NN
  was/VBD
  transport

(S
  An/DT
  Executive/JJ
  Staff/NNP
  member/NN
  reports/NNS
  #/#
  #/#
  #/#
  #/#
  students/NNS
  gained/VBD
  access/NN
  to/TO
  an/DT
  employee/NN
  's/POS
  #/#
  #/#
  #/#
  #/#
  #/#
  and/CC
  forwarded/VBD
  inappropriate/JJ
  images/NNS
  to/TO
  a/DT
  social/JJ
  media/NNS
  platform/NN
  ./.
  (PERSON Parents/NNS)
  will/MD
  be/VB
  contacted/VBN
  and/CC
  supports/NNS
  are/VBP
  in/IN
  place/NN
  for/IN
  the/DT
  students/NNS
  and/CC
  employee/NN
  ./.
  (PERSON Media/NNP Unit/NNP)
  and/CC
  (PERSON Director/NNP)
  ,/,
  (ORGANIZATION Educational/NNP Leadership/NNP)
  will/MD
  be/VB
  informed/VBN
  ./.)
(S
  A/DT
  student/NN
  has/VBZ
  disclosed/VBN
  that/IN
  another/DT
  student/NN
  has/VBZ
  allegedly/RB
  inappropriately/RB
  assaulted/JJ
  #/#
  #/#
  #/#
  #/#
  ./.
  The/DT
  school/NN
  is/VBZ
  continuing/VBG
  to/TO
  monitor/VB
  ./.
  Supports/NNS
  are/VBP
  in/IN
  place/NN
  for/IN
  students/NNS
  ./.)
(S
  Executive/JJ
  staff/NN
  re

...

(S
  The/DT
  school/NN
  reported/VBD
  a/DT
  student/NN
  's/POS
  violent/JJ
  behaviour/NN
  on/IN
  school/NN
  grounds/NNS
  ./.
  The/DT
  student/NN
  damaged/VBD
  school/NN
  property/NN
  while/IN
  in/IN
  a/DT
  heightened/JJ
  state/NN
  ./.
  Police/NNP
  were/VBD
  called/VBN
  and/CC
  attended/VBD
  the/DT
  school/NN
  ./.
  The/DT
  student/NN
  has/VBZ
  since/IN
  been/VBN
  conveyed/VBN
  xxxxx/NNP
  ./.
  The/DT
  matter/NN
  is/VBZ
  being/VBG
  managed/VBN
  locally/RB
  ./.)
(S
  An/DT
  executive/JJ
  staff/NN
  member/NN
  has/VBZ
  reported/VBN
  allegations/NNS
  that/IN
  a/DT
  student/NN
  has/VBZ
  indecently/RB
  assaulted/VBN
  another/DT
  student/NN
  on/IN
  school/NN
  grounds/NNS
  ./.
  Police/NNS
  have/VBP
  been/VBN
  notified/VBN
  ./.
  (PERSON Parents/NNS)
  will/MD
  be/VB
  advised/VBN
  ./.
  #/#
  #/#
  #/#
  #/#
  is/VBZ
  being/VBG
  followed/VBN
  and/CC
  support/NN
  is/VBZ
  in/IN
  place/NN
  ./.
  Director/NNP
  ,/,
  (ORGAN

(S
  The/DT
  school/NN
  reported/VBD
  concerns/NNS
  about/IN
  a/DT
  video/NN
  on/IN
  social/JJ
  media/NNS
  containing/VBG
  graphic/JJ
  content/NN
  ,/,
  which/WDT
  has/VBZ
  been/VBN
  viewed/VBN
  by/IN
  students/NNS
  ./.
  Supports/NNS
  are/VBP
  being/VBG
  organised/VBN
  ./.)
(S
  Executive/JJ
  staff/NN
  reports/VBZ
  a/DT
  student/NN
  was/VBD
  found/VBN
  in/IN
  possession/NN
  of/IN
  a/DT
  weapon/NN
  and/CC
  has/VBZ
  proceeded/VBN
  to/TO
  threaten/VB
  another/DT
  student/NN
  on/IN
  school/NN
  grounds/NNS
  ./.
  No/DT
  injuries/NNS
  sustained/VBN
  ./.
  Parents/NNS
  were/VBD
  contacted/VBN
  ./.
  Police/NNP
  were/VBD
  notified/VBN
  and/CC
  arrived/VBN
  on/IN
  site/NN
  ,/,
  the/DT
  weapon/NN
  was/VBD
  confiscated/VBN
  ./.
  Ambulance/NNP
  were/VBD
  contacted/VBN
  and/CC
  the/DT
  student/NN
  was/VBD
  conveyed/VBN
  to/TO
  hospital/VB
  accompanied/VBN
  by/IN
  a/DT
  carer/NN
  ./.
  (PERSON Medical/NNP)
  treatment/NN


(S
  A/DT
  student/NN
  allegedly/RB
  (ORGANIZATION XXXX/NNP)
  another/DT
  student/NN
  over/IN
  clothing/NN
  ./.
  All/DT
  #/#
  #/#
  #/#
  #/#
  guidelines/NNS
  have/VBP
  been/VBN
  followed/VBN
  ./.)
(S
  An/DT
  employee/NN
  reports/VBZ
  a/DT
  student/NN
  was/VBD
  in/IN
  possession/NN
  of/IN
  a/DT
  weapon/NN
  on/IN
  school/NN
  grounds/NNS
  ./.
  No/DT
  threats/NNS
  were/VBD
  made/VBN
  and/CC
  no/DT
  injuries/NNS
  were/VBD
  sustained/VBN
  ./.
  The/DT
  parents/NNS
  were/VBD
  contacted/VBN
  and/CC
  the/DT
  weapon/NN
  was/VBD
  collected/VBN
  by/IN
  parents/NNS
  ./.
  The/DT
  employee/NN
  further/RB
  reported/VBD
  concerns/NNS
  for/IN
  the/DT
  students/NNS
  wellbeing/VBG
  ./.
  Supports/NNS
  will/MD
  be/VB
  put/VBN
  in/IN
  place/NN
  on/IN
  school/NN
  grounds/NNS
  ./.
  #/#
  #/#
  #/#
  #/#
  has/VBZ
  been/VBN
  followed/VBN
  ./.
  The/DT
  Director/NNP
  ,/,
  (ORGANIZATION Educational/NNP Leadership/NNP)
  will/MD
  be/V

(S
  A/DT
  student/NN
  has/VBZ
  sustained/VBN
  an/DT
  injury/NN
  after/IN
  being/VBG
  assaulted/VBN
  by/IN
  another/DT
  student/NN
  on/IN
  school/NN
  grounds/NNS
  ./.
  First/NNP
  aid/NN
  applied/VBN
  ./.
  (ORGANIZATION Parents/NNS)
  and/CC
  emergency/NN
  services/NNS
  were/VBD
  notified/VBN
  ./.
  (PERSON Student/NN)
  was/VBD
  transported/VBN
  to/TO
  hospital/VB
  via/IN
  ambulance/NN
  in/IN
  a/DT
  xxxxx/JJ
  xxxxx/NN
  ./.
  Executive/JJ
  staff/NN
  are/VBP
  aware/JJ
  ./.
  Director/NNP
  ,/,
  (ORGANIZATION Educational/NNP Leadership/NNP)
  will/MD
  be/VB
  notified/VBN
  ./.)


TypeError: expected string or bytes-like object

In [10]:
nltk.download('averaged_perceptron_tagger')

[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     C:\Users\MOC\AppData\Roaming\nltk_data...
[nltk_data]   Unzipping taggers\averaged_perceptron_tagger.zip.


True

In [12]:
nltk.download('maxent_ne_chunker')

[nltk_data] Downloading package maxent_ne_chunker to
[nltk_data]     C:\Users\MOC\AppData\Roaming\nltk_data...
[nltk_data]   Unzipping chunkers\maxent_ne_chunker.zip.


True

In [14]:
nltk.download('words')

[nltk_data] Downloading package words to
[nltk_data]     C:\Users\MOC\AppData\Roaming\nltk_data...
[nltk_data]   Unzipping corpora\words.zip.


True

In [2]:
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer

# 读取表格数据
data = pd.read_csv('2019-2021.csv')

# 处理缺失值，将NaN替换为空字符串
data['Summary of the Incident (External Distribution)'].fillna('', inplace=True)

# 提取Summary of the Incident列的文本数据
summaries = data['Summary of the Incident (External Distribution)'].tolist()

# 使用TF-IDF算法提取关键词
vectorizer = TfidfVectorizer()
tfidf_matrix = vectorizer.fit_transform(summaries)
feature_names = vectorizer.get_feature_names()

# 遍历每个文本的关键词
for i in range(len(summaries)):
    summary = summaries[i]
    feature_index = tfidf_matrix[i].nonzero()[1]
    keywords = [feature_names[index] for index in feature_index]
    
    # 输出包含与时序相关的关键词
    time_keywords = [keyword for keyword in keywords if 'date' in keyword or 'time' in keyword]
    if time_keywords:
        print(f"Summary {i+1}:")
        print(summary)
        print("Time-related Keywords:", time_keywords)
        print()


D:\anaconda3\lib\site-packages\sklearn\utils\deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)


Summary 67:
An Executive staff member reports students involved in a physical altercation on school grounds. The school was placed into lock down, and released a short time later. First aid was not required. Parents have been contacted. The school is managing the matter. Director Educational Leadership will be made aware.
Time-related Keywords: ['time']

Summary 74:
An Executive staff member reports a physical altercation between students on school grounds. First aid was not required. The school was placed into lock down and released a short time later. Parents and care givers were notified. The school is managing the matter. Supports are in place. Director, Educational Leadership will be made aware.
Time-related Keywords: ['time']

Summary 78:
Employee reports #### students have absconded school grounds. Carers have been informed. Students have not been found at the time of reporting. Police have not been called. Supports are in place. Executive staff are aware. Director, Educational 

Summary 2456:
Executive staff member reports that a student has been away from school for a period of time. Police are aware and will investigate. The student previously disclosed the use of illicit substances off school grounds. #### has been followed and supports will be organised. Director, Educational Leadership will be informed.
Time-related Keywords: ['time']

Summary 2488:
Executive staff reports that three students were found in possession of an illicit substance on school grounds.  The school went into a lockdown for a period of time but is now fully operational. Police attended. An ambulance was contacted as a student sustained an injury after damaging school property. First aid was administered and paramedics cleared the student. The school are managing the matter and supports are in place. #### has been followed. Director Educational Leadership is aware.
Time-related Keywords: ['time']

Summary 2496:
Employee reports XXXX students have absconded school grounds. The students

Summary 5063:
Student arrived late to school and was questioned by the Deputy Principal. Student refused to a bag check but made a statement confessing to illicit substances in the bag. Police arrived at school in regards to a different incident and searched the student's bag seizing a large amount of illicit substances. Student's parents were called. Parents had a meeting with the principal at this time the student left school grounds. Parents agreed they would look for him.
Time-related Keywords: ['time']

Summary 5064:
Two students have been ###### ###### after a physical altercation and ###### ###### an ###### to each other and staff. Employee sustained minor injuries. No time taken off ###### ###### ###### ######.
Time-related Keywords: ['time']

Summary 5133:
An employee sustained an injury ###### a student ###### ###### ######. First aid was not required at the time. The employee is ###### ###### ###### ###### ###### ###### and the ###### is aware.
Time-related Keywords: ['time'

Summary 7282:
Student was in a heightened state and was verbally and physically aggressive towards staff. The student tried to abscond from the off site activity. Staff spent time trying to calm the student. Parents contacted and picked the student up. The school is managing the matter and the student?s #### will be reviewed.
Time-related Keywords: ['time']

Summary 7324:
A student located and ########## on school grounds. Parents were contacted. #### #### #### #### and the student was #### #### #### ####. #### the student was fine and able to remain at school. The school is undertaking a #####at this time.
Time-related Keywords: ['time']

Summary 7326:
A student has been found in possession of a weapon on school grounds. No injuries sustained. The weapon may have been discarded, its location is unknown at time of reporting. Parents have been notified and have conveyed the student home. Police will be notified.
Time-related Keywords: ['time']

Summary 7348:
A student became #### and le

In [5]:
import re
from datetime import datetime
import pandas as pd

# 读取CSV文件
df = pd.read_csv('2019-2021.csv')

# 从"Summary of the Incident"列中提取日期时间信息
summary_column = 'Summary of the Incident (External Distribution)'
summaries = df[summary_column].tolist()

# 定义日期时间的正则表达式模式
pattern = r'(\d{1,2}/\d{1,2}/\d{4} \d{1,2}:\d{2})'

# 提取日期时间信息
date_time_objects = []
for summary in summaries:
    matches = re.findall(pattern, str(summary))
    for match in matches:
        dt_obj = datetime.strptime(match, '%d/%m/%Y %H:%M')
        date_time_objects.append(dt_obj)

# 打印提取的日期时间信息
for i, dt_obj in enumerate(date_time_objects):
    print(f"Row {i+1}: {dt_obj}")
